In [79]:
## 조선일보 크롤링
import os
import requests
from bs4 import BeautifulSoup
from datetime import datetime, timedelta
import csv
from tqdm import tqdm  # tqdm 추가
from multiprocessing import Pool
from concurrent.futures import ThreadPoolExecutor, as_completed 
import time
import json

## 2024년부터 오늘 날짜 까지 클롤링실시 연합은 2일치만 해도 만개가 넘는다.. 너무큼 
start_date = datetime(2024, 1, 1)
end_date = datetime(2024, 1, 2)
# end_date = datetime.now()  
#end_date = datetime.now() - timedelta(days=12) ## 연합은 업데이트가 좀 느려서 간격을 둠 

limit = 5

## 날짜 형식을 바꿔주는 함수 
def date_range(start, end):
    for n in range(int((end - start).days) + 1):
        yield start + timedelta(n)

def fetch_news_articles(url):
    response = requests.get(url, timeout=10)
    response.raise_for_status()
    soup = BeautifulSoup(response.text, 'html.parser')
    story = soup.find('ul', class_='list')
    urls = [a['href'] for a in story.find_all('a')] if story else []
    return urls

#제목 기사 url 추출함수
def fetch_articles_with_details(url):
    try:
        response = requests.get(url,timeout = limit)
        response.raise_for_status()  # HTTP 에러가 있을 경우 예외를 발생시킵니다.

        soup = BeautifulSoup(response.text, 'html.parser')
        articles = []
        
        # 제목 추출
        script = soup.find('script', id='contentJsonData').text
        try:
            # JSON 데이터 파싱
            first_brace_index = script.find('{')
            start = script.find('{', first_brace_index + 1)
            end = script.find('}') + 1
            json_data = json.loads(script[start:end])

            # 제목과 본문 추출
            title = json_data['TITLE']
            text_content = json_data['BODY']
            text_content = text_content.replace('\n', ' ')
            print(url)
            articles.append([url, title, text_content])
        except (json.JSONDecodeError, KeyError) as e:
            print(f"Error parsing JSON data for URL {url}: {e}")
            
        return articles
    except requests.exceptions.Timeout:
        print("Timeout occurred while fetching articles from", url)
        return []
    except requests.exceptions.RequestException as e:
        print("Error occurred while fetching articles:", e)
        return []

    
    
# 크롤링하고 결과를 바로 CSV 파일에 저장하는 함수
def hap_crawler():
    # 결과를 저장할 폴더 생성
    result_dir = 'result'
    if not os.path.exists(result_dir):
        os.makedirs(result_dir)

    # CSV 파일 경로 설정
    csv_file_path = os.path.join(result_dir, 'yeonhap_news(test).csv')
    
    # CSV 파일을 열고 데이터를 저장합니다.
    with open(csv_file_path, 'w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        # CSV 파일의 헤더를 작성합니다.
        writer.writerow(['URL', 'Title', 'Content'])
            
        # 멀티쓰레드로 
        with ThreadPoolExecutor(max_workers=16) as executor:
            future_to_url = {}
            
            # 모든 날짜에 대해 URL을 생성하고 크롤링을 실행
            for single_date in date_range(start_date, end_date):
                formatted_date = single_date.strftime("%Y/%m/%d")
                for i in range(1, 3):  # 여기서는 예시로 하루에 두 개의 URL을 생성합니다.
                    url = f'https://www.yna.co.kr/sitemap/articles/{formatted_date}-{i}.htm'

                    # 해당 날짜의 기사 links 리스트 추출
                    links = fetch_news_articles(url)
                    #print(f"Date: {formatted_date} - Fetched {len(links)} articles")

                    # 각 링크에 대해 비동기 작업을 예약합니다.
                    for link in links:
                        future = executor.submit(fetch_articles_with_details, link)
                        future_to_url[future] = link

            # 완료된 작업을 순서대로 처리합니다.
            for future in as_completed(future_to_url):
                articles = future.result()
                if articles:
                    for article in articles:
                        writer.writerow(article)
                #print(f"Completed: {future_to_url[future]}")
                
# # CSV 파일 저장
# 2일하는데,5
if __name__ == "__main__":
    start_time = time.time()  # 코드 실행 시작 시간 기록
    hap_crawler()
    end_time = time.time()  # 코드 실행 종료 시간 기록
    print(f"Execution time: {end_time - start_time} seconds")  # 실행 시간 출력


https://www.yna.co.kr/view/AKR20240101000100011
Error occurred while fetching articles: ('Connection aborted.', ConnectionResetError(10054, '현재 연결은 원격 호스트에 의해 강제로 끊겼습니다', None, 10054, None))
https://www.yna.co.kr/view/MYH20231229011400704
https://www.yna.co.kr/view/AKR20231230039500017
https://www.yna.co.kr/view/MYH20240101000100641
https://www.yna.co.kr/view/AKR20231229135800001
https://www.yna.co.kr/view/AKR20240101000600071https://www.yna.co.kr/view/MYH20240101000200641

https://www.yna.co.kr/view/AKR20240101000500060
https://www.yna.co.kr/view/AKR20240101000700004
https://www.yna.co.kr/view/AKR20231229141700530
https://www.yna.co.kr/view/AKR20240101000200051
https://www.yna.co.kr/view/AKR20240101001000072
https://www.yna.co.kr/view/AKR20231231027152007
https://www.yna.co.kr/view/AKR20231229107400704
https://www.yna.co.kr/view/AKR20240101001200004
https://www.yna.co.kr/view/AKR20240101001800005
https://www.yna.co.kr/view/AKR20240101001100079
https://www.yna.co.kr/view/AKR20240101002

https://www.yna.co.kr/view/AKR20231229113000053
https://www.yna.co.kr/view/AKR20240101014600062
https://www.yna.co.kr/view/AKR20231229108100001https://www.yna.co.kr/view/AKR20240101016300005

https://www.yna.co.kr/view/AKR20240101015500003
https://www.yna.co.kr/view/AKR20240101014000004
https://www.yna.co.kr/view/AKR20240101016500007
https://www.yna.co.kr/view/AKR20240101015100009https://www.yna.co.kr/view/MYH20240101000400641

https://www.yna.co.kr/view/AKR20240101016400005
https://www.yna.co.kr/view/AKR20231229086900064
https://www.yna.co.kr/view/AKR20231229091800061
https://www.yna.co.kr/view/AKR20240101014700504
https://www.yna.co.kr/view/MYH20240101000500641
https://www.yna.co.kr/view/AKR20231229116300057
https://www.yna.co.kr/view/MYH20240101004700641
https://www.yna.co.kr/view/AKR20240101017000003https://www.yna.co.kr/view/AKR20240101015600001

https://www.yna.co.kr/view/AKR20240101017100504
https://www.yna.co.kr/view/AKR20240101017700075
https://www.yna.co.kr/view/AKR2024010101

https://www.yna.co.kr/view/AKR20240101028200052
https://www.yna.co.kr/view/MYH20240101004500641
https://www.yna.co.kr/view/MYH20240101004600641
https://www.yna.co.kr/view/MYH20240101006600641
https://www.yna.co.kr/view/AKR20240101030000074https://www.yna.co.kr/view/AKR20240101028800001

https://www.yna.co.kr/view/AKR20240101029600530
https://www.yna.co.kr/view/AKR20240101028400001
https://www.yna.co.kr/view/MYH20240101006400641
https://www.yna.co.kr/view/MYH20240101006500641
https://www.yna.co.kr/view/MYH20240101006700641
https://www.yna.co.kr/view/AKR20240101030100084https://www.yna.co.kr/view/AKR20240101029900009

https://www.yna.co.kr/view/AKR20240101029800003
https://www.yna.co.kr/view/AKR20240101028700074
https://www.yna.co.kr/view/MYH20240101007200704
https://www.yna.co.kr/view/AKR20240101029500001https://www.yna.co.kr/view/MYH20240101007400641
https://www.yna.co.kr/view/MYH20240101007300641

https://www.yna.co.kr/view/MYH20240101007100641https://www.yna.co.kr/view/AKR20240101030

https://www.yna.co.kr/view/MYH20240101015400641
https://www.yna.co.kr/view/MYH20240101015300641
https://www.yna.co.kr/view/AKR20240101039500007
https://www.yna.co.kr/view/MYH20240101015200641
https://www.yna.co.kr/view/AKR20240101045200063
https://www.yna.co.kr/view/AKR20240101045300080https://www.yna.co.kr/view/MYH20240101015600641
https://www.yna.co.kr/view/AKR20240101045100062

https://www.yna.co.kr/view/MYH20240101015500032https://www.yna.co.kr/view/MYH20240101015900641
https://www.yna.co.kr/view/MYH20240101015800641

https://www.yna.co.kr/view/AKR20240101041151007
https://www.yna.co.kr/view/AKR20240101045700052
https://www.yna.co.kr/view/MYH20240101015700641https://www.yna.co.kr/view/AKR20240101045600063

https://www.yna.co.kr/view/AKR20240101045400009
https://www.yna.co.kr/view/MYH20240101016200641
https://www.yna.co.kr/view/AKR20240101045000504
https://www.yna.co.kr/view/MYH20240101016100641
https://www.yna.co.kr/view/MYH20240101016000641
https://www.yna.co.kr/view/AKR2023123004

https://www.yna.co.kr/view/MYH20240102002600641
https://www.yna.co.kr/view/AKR20240102010500504
https://www.yna.co.kr/view/AKR20240102014800051https://www.yna.co.kr/view/AKR20240102010100505

https://www.yna.co.kr/view/AKR20240102013200004https://www.yna.co.kr/view/AKR20231229085500065

https://www.yna.co.kr/view/AKR20231227127800054
https://www.yna.co.kr/view/AKR20231226063000054
https://www.yna.co.kr/view/AKR20231227031500054https://www.yna.co.kr/view/MYH20240102002700641
https://www.yna.co.kr/view/AKR20231227094400054

https://www.yna.co.kr/view/AKR20231215114800004
https://www.yna.co.kr/view/AKR20231229090900054
https://www.yna.co.kr/view/AKR20231227116500054
https://www.yna.co.kr/view/AKR20240102009000505
https://www.yna.co.kr/view/MYH20240102002800641
https://www.yna.co.kr/view/AKR20240101040200063https://www.yna.co.kr/view/AKR20240101053351057

https://www.yna.co.kr/view/AKR20240102016500030https://www.yna.co.kr/view/AKR20240102014700005https://www.yna.co.kr/view/AKR202401020175

...

https://www.yna.co.kr/view/AKR20240605158751099
https://www.yna.co.kr/view/AKR20240606003700071
https://www.yna.co.kr/view/AKR20240606002500081
https://www.yna.co.kr/view/AKR20240606003100087
https://www.yna.co.kr/view/AKR20240606002100081
https://www.yna.co.kr/view/AKR20240606003500109https://www.yna.co.kr/view/AKR20240606003900072

https://www.yna.co.kr/view/AKR20240606004200091
https://www.yna.co.kr/view/AKR20240606005400108
https://www.yna.co.kr/view/AKR20240606005351091
https://www.yna.co.kr/view/AKR20240606004800071
https://www.yna.co.kr/view/AKR20240606006900009
https://www.yna.co.kr/view/AKR20240606006100071
https://www.yna.co.kr/view/AKR20240605168552075
https://www.yna.co.kr/view/AKR20240605156000001
https://www.yna.co.kr/view/AKR20240606006200072
https://www.yna.co.kr/view/AKR20240606005800071
https://www.yna.co.kr/view/AKR20240606007051072
https://www.yna.co.kr/view/AKR20240605161700530
https://www.yna.co.kr/view/AKR20240606007052072
https://www.yna.co.kr/view/AKR2024060507

https://www.yna.co.kr/view/MYH20240606001500641
https://www.yna.co.kr/view/MYH20240606001200641
https://www.yna.co.kr/view/AKR20240606024400003
https://www.yna.co.kr/view/MYH20240606001300641
https://www.yna.co.kr/view/AKR20240606024500054https://www.yna.co.kr/view/MYH20240606001600641
https://www.yna.co.kr/view/AKR20240606024300030

https://www.yna.co.kr/view/AKR20240605078600064
https://www.yna.co.kr/view/AKR20240606025800054https://www.yna.co.kr/view/AKR20240606025100030

https://www.yna.co.kr/view/AKR20240606013151504
https://www.yna.co.kr/view/AKR20240606025300053
https://www.yna.co.kr/view/AKR20240606019700009
https://www.yna.co.kr/view/MYH20240606001700641
https://www.yna.co.kr/view/AKR20240605117700051https://www.yna.co.kr/view/AKR20240606026800030

https://www.yna.co.kr/view/AKR20240605125500051
https://www.yna.co.kr/view/AKR20240606026700007
https://www.yna.co.kr/view/AKR20240606019900003
https://www.yna.co.kr/view/AKR20240606026300075
https://www.yna.co.kr/view/AKR2024060602

https://www.yna.co.kr/view/MYH20240606006400641
https://www.yna.co.kr/view/GYH20240606000200044
https://www.yna.co.kr/view/MYH20240606005800641
https://www.yna.co.kr/view/MYH20240606006700641
https://www.yna.co.kr/view/MYH20240606006500032
https://www.yna.co.kr/view/MYH20240606006600032
https://www.yna.co.kr/view/AKR20240606038200007
https://www.yna.co.kr/view/AKR20240606040500062
https://www.yna.co.kr/view/MYH20240606006800641
https://www.yna.co.kr/view/MYH20240606006900641
https://www.yna.co.kr/view/AKR20240606041200007
https://www.yna.co.kr/view/AKR20240606040800007
https://www.yna.co.kr/view/AKR20240606039300003
https://www.yna.co.kr/view/MYH20240606007100641
https://www.yna.co.kr/view/AKR20240606037651009
https://www.yna.co.kr/view/MYH20240606007200704
https://www.yna.co.kr/view/MYH20240606007000641https://www.yna.co.kr/view/AKR20240606040700008

https://www.yna.co.kr/view/AKR20240606039200017
https://www.yna.co.kr/view/AKR20240606040900003
https://www.yna.co.kr/view/GYH2024060600

https://www.yna.co.kr/view/AKR20240606059000073
https://www.yna.co.kr/view/GYH20240606000600044
https://www.yna.co.kr/view/AKR20240606060700527https://www.yna.co.kr/view/AKR20240606052700504
https://www.yna.co.kr/view/AKR20240606058051007

https://www.yna.co.kr/view/AKR20240605162251098
https://www.yna.co.kr/view/AKR20240606060800527
https://www.yna.co.kr/view/AKR20240606063100007
https://www.yna.co.kr/view/AKR20240605163851007
https://www.yna.co.kr/view/MYH20240606014400641https://www.yna.co.kr/view/AKR20240606063200003
https://www.yna.co.kr/view/AKR20240606055100009

https://www.yna.co.kr/view/AKR20240606064200007
https://www.yna.co.kr/view/AKR20240606063800007
https://www.yna.co.kr/view/AKR20240606064100052
https://www.yna.co.kr/view/MYH20240606002300528
https://www.yna.co.kr/view/AKR20240606063600007
https://www.yna.co.kr/view/AKR20240606062200003
https://www.yna.co.kr/view/AKR20240606054300004
https://www.yna.co.kr/view/AKR20240605165351007
https://www.yna.co.kr/view/MYH2024060601

JSONDecodeError: Unterminated string starting at: line 4 column 10 (char 103)